In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/nsutai/sample_submission.csv
/kaggle/input/nsutai/train.csv
/kaggle/input/nsutai/test.csv


In [2]:
from catboost import CatBoostRegressor
from sklearn.model_selection import ShuffleSplit, GridSearchCV
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, cross_val_score, cross_val_predict
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

In [3]:
df = pd.read_csv('../input/nsutai/train.csv')
# df = df.drop('name',axis=1)
# df = df.drop('sentry_object',axis=1)
df = df.drop('event',axis=1)
df = df.drop('id',axis=1)
terms = 0
total = 0
for i in df:
    df[i].fillna(value=df[i].mean(), inplace=True)
df['px12'] = df.px1 * df.px2
df['Q12'] = df.q1 * df.q2
df['phi12'] = df.phi1 * df.phi2
df['eta12'] = df.eta1 * df.eta2
df['pt12'] = df.pt1 * df.pt2
df['E12'] = df.e1 * df.e2
df['pz_diff'] = df.pz1 - df.pz2
df['eta_diff'] = df.eta1 - df.eta2

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 69940 entries, 0 to 69939
Data columns (total 25 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   e1        69940 non-null  float64
 1   px1       69940 non-null  float64
 2   py1       69940 non-null  float64
 3   pz1       69940 non-null  float64
 4   pt1       69940 non-null  float64
 5   eta1      69940 non-null  float64
 6   phi1      69940 non-null  float64
 7   q1        69940 non-null  int64  
 8   e2        69940 non-null  float64
 9   px2       69940 non-null  float64
 10  py2       69940 non-null  float64
 11  pz2       69940 non-null  float64
 12  pt2       69940 non-null  float64
 13  eta2      69940 non-null  float64
 14  phi2      69940 non-null  float64
 15  q2        69940 non-null  int64  
 16  mass      69940 non-null  float64
 17  px12      69940 non-null  float64
 18  Q12       69940 non-null  int64  
 19  phi12     69940 non-null  float64
 20  eta12     69940 non-null  fl

In [5]:
Xn_data = np.array(df.drop('mass', axis = 1).values)
# Normalize X_data
X_data = (Xn_data - np.mean(Xn_data)) / np.std(Xn_data)
# y_data = np.log(np.array(df["mass"]))
from sklearn.preprocessing import StandardScaler

In [6]:
X = df.drop('mass',axis=1)
# from sklearn.preprocessing import StandardScaler
# sc = StandardScaler()
# X = sc.fit_transform(X)
y = df['mass'].values

X_train, X_test, y_train, y_test = train_test_split(X_data,y,test_size=0.2,random_state=33)
ss = StandardScaler()
X_train = ss.fit_transform(X_train)
X_test = ss.fit_transform(X_test)

In [7]:
X_train

array([[ 1.54406036e-03,  5.00046796e-02,  9.72291485e-01, ...,
         3.46918585e-03, -4.15573889e-02, -7.97763559e-03],
       [ 1.94422910e-04, -3.33701351e-01, -1.21056344e+00, ...,
         3.65737676e-03, -1.13711783e-01,  2.60815651e-03],
       [ 2.38266960e-03,  5.19004764e-01,  8.78117565e-01, ...,
         2.62745940e-03,  8.97889389e-02, -2.15806071e-02],
       ...,
       [-1.40730483e-04, -1.79267428e-01,  1.03092574e+00, ...,
         3.74511846e-03, -2.07740905e+00,  7.78566082e-03],
       [-8.58332036e-04, -7.98378259e-01, -1.12113137e+00, ...,
         2.87497174e-03,  4.31631201e-01,  8.14307267e-04],
       [ 1.02554766e-03, -1.28674581e+00, -1.34946525e-01, ...,
         3.44007559e-03,  2.95152031e-03, -5.08424031e-04]])

In [8]:
#List of categorical columns
# categoricalcolumns = X.select_dtypes(include=["object"]).columns.tolist()
# print("Names of categorical columns : ", categoricalcolumns)
#Get location of categorical columns
cat_features = ['q1','q2','Q12']
print("Location of categorical columns : ",cat_features)


Location of categorical columns :  ['q1', 'q2', 'Q12']


In [9]:
# importing Pool
from catboost import Pool
#Creating pool object for train dataset. we give information of categorical fetures to parameter cat_fetaures
train_data = Pool(data=X_train,
                  label=y_train,
#                   cat_features=cat_features
                 )
#Creating pool object for test dataset
test_data = Pool(data=X_test,
                  label=y_test,
#                   cat_features=cat_features
                 )

In [10]:
# print(np.sqrt(error))

In [11]:
catbr = CatBoostRegressor(verbose=5000,task_type='GPU',loss_function='RMSE',iterations = 20000,depth = 12).fit(X_train,y_train)
# R2CV = cross_val_score(catbr,X_test,y_test,cv=3,scoring="r2").mean()
error = -cross_val_score(catbr,X_test,y_test,cv=2,scoring="neg_mean_squared_error").mean()
# print(R2CV)
print(np.sqrt(error))

Learning rate set to 0.011444
0:	learn: 1.0109453	total: 25.3ms	remaining: 8m 25s
5000:	learn: 0.2627569	total: 1m 41s	remaining: 5m 3s
10000:	learn: 0.0976646	total: 3m 22s	remaining: 3m 22s
15000:	learn: 0.0396183	total: 5m 4s	remaining: 1m 41s
19999:	learn: 0.0169753	total: 6m 44s	remaining: 0us
Learning rate set to 0.008715
0:	learn: 1.0111765	total: 32ms	remaining: 10m 39s
5000:	learn: 0.5784365	total: 12m 45s	remaining: 38m 15s
10000:	learn: 0.5133532	total: 25m 6s	remaining: 25m 5s
15000:	learn: 0.4772074	total: 37m 26s	remaining: 12m 28s
19999:	learn: 0.4527199	total: 49m 6s	remaining: 0us
Learning rate set to 0.008715
0:	learn: 1.0070361	total: 76.6ms	remaining: 25m 31s
5000:	learn: 0.5676638	total: 12m 51s	remaining: 38m 33s
10000:	learn: 0.5046212	total: 23m 32s	remaining: 23m 32s
15000:	learn: 0.4696909	total: 34m 21s	remaining: 11m 26s
19999:	learn: 0.4463740	total: 45m 11s	remaining: 0us
0.8447744377236096


In [12]:
# params = {
    
#     "depth": [2, 3, 4, 5, 6],
#     "learning_rate": [0.1, 0.01, 0.5]
# }

In [13]:
# cv = GridSearchCV(catbr, params, cv=10, verbose=True).fit(X_train, y_train)
# print(cv.best_params_)

In [14]:
# catbrtuned = CatBoostRegressor(depth=5,learning_rate=0.01,verbose=False,task_type='GPU').fit(X_train,y_train)

# # R2CVtuned = cross_val_score(catbrtuned,X_test,y_test,cv=15,scoring="r2").mean()
# # print(R2CVtuned)
# errortuned = -cross_val_score(catbrtuned,X_test,y_test,cv=20,scoring="neg_mean_squared_error").mean()
# print(np.sqrt(errortuned))

In [15]:
X_test

array([[ 1.01680714e-02,  6.52076470e-01, -1.71361082e+00, ...,
         1.49118772e-03,  1.63726624e-01,  3.10255375e-03],
       [ 1.24653160e-02,  1.40030095e-01,  9.08963077e-01, ...,
         6.54264303e-04,  1.87932998e+00, -2.37996666e-02],
       [ 1.56609992e+00,  3.08161424e-01, -3.38753181e-01, ...,
        -4.62755342e-02,  1.25592922e+00, -1.43120765e-02],
       ...,
       [ 8.24693308e-03, -1.65144148e-01, -1.91790940e+00, ...,
         1.21247452e-04,  1.06549128e+00,  3.83478623e-03],
       [ 9.59390026e-05, -1.42118970e+00, -6.56800351e-01, ...,
         5.07400206e-04, -1.61068698e+00,  1.05205829e-03],
       [ 2.32941353e-03,  1.13598956e-01, -1.35239977e-01, ...,
         8.06554653e-04, -4.00680340e-01, -5.26439826e-03]])

In [16]:
test=pd.read_csv("../input/nsutai/test.csv")

X_test=test.drop('id',axis=1)
X_test = X_test.drop('event',axis=1)
# X_test = X_test.drop('id',axis=1)

X_test

e1        px1       py1       pz1       pt1       eta1      phi1  \
0      3.900910  24.920700 -1.102674  0.702628  24.98810 -42.967949 -0.073422   
1     -3.401169  -7.007870  0.581511  0.321741   8.03705  -0.162631  2.629960   
2      0.804254  -1.219560  1.557146  0.949164  12.61310   0.337772 -1.667640   
3      1.073530  -2.721070  1.258642  0.268368   2.75403   3.670449 -2.986720   
4      0.704689  16.055100  1.471738 -0.863552  17.32390   2.430194  0.385110   
...         ...        ...       ...       ...       ...        ...       ...   
29970 -0.258829 -10.658000 -0.507161  0.228920  11.84330   0.296608  2.690370   
29971 -0.405636   7.854990  1.024085 -0.860718  17.05020  -0.456347  1.092010   
29972  1.719597  -3.273500  1.397346  0.577056   3.28801  -1.215898 -3.047630   
29973  1.764202  11.352600  0.815074  0.930537  16.43280  -0.126448  0.808132   
29974  4.601752   0.886162  0.556092  0.994464   5.55010  -2.074547  1.410440   

       q1         e2       px2        py2       pz2       pt2      eta2  \
0      -1   0.726854  0.715108  -0.374241 -1.351969 -0.654767  0.674536   
1       1  36.603944  0.698290   0.936158 -0.772930  0.828964  0.647576   
2       1 -25.401295  0.615361   0.550970  0.397435 -0.525276  0.723704   
3      -1 -42.101333  0.741327   0.236630 -0.151015  0.472083  0.974790   
4      -1  -1.048602  0.958089   0.268982 -0.264064 -0.969478  0.554407   
...    ..        ...       ...        ...       ...       ...       ...   
29970  -1  -4.251468  0.813939  73.667501  1.158823 -0.148324  0.954442   
29971   1  -1.616737  0.550067   1.162549 -0.311051 -0.897992  0.772986   
29972   1   0.628021  0.542946   0.143970 -0.731390 -0.307851  0.734795   
29973  -1  -1.111305  0.932663  -0.063397 -0.153664 -0.999193  0.545050   
29974   1  -3.578146  0.628637  -9.284831  0.425168  0.147698  0.555115   

           phi2  q2  
0     -0.987639  -1  
1     -0.532239  -1  
2      0.481615   1  
3      0.356768  -1  
4     -0.101867  -1  
...         ...  ..  
29970  0.388798   1  
29971 -0.527932   1  
29972 -0.766423  -1  
29973  0.121883   1  
29974  0.964454  -1  

[29975 rows x 16 columns]

In [17]:
X_test['px12'] = X_test.px1 * X_test.px2
X_test['Q12'] = X_test.q1 * X_test.q2
X_test['phi12'] = X_test.phi1 * X_test.phi2
X_test['eta12'] = X_test.eta1 * X_test.eta2
X_test['pt12'] = X_test.pt1 * X_test.pt2
X_test['E12'] = X_test.e1 * X_test.e2
X_test['pz_diff'] = X_test.pz1 - X_test.pz2
X_test['eta_diff'] = X_test.eta1 - X_test.eta2
y_pred=catbr.predict(X_test)
sample_submission=pd.read_csv("../input/nsutai/sample_submission.csv")
sample_submission['mass']=y_pred
sample_submission.to_csv('submission.csv',index=False)